In [1]:
import pandas as pd
import numpy as np
import os
import sumolib
import copy
from tqdm import tqdm
from datetime import datetime

In [2]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fmins = range(midnight, next_day, 300)
m = 100 # m ranges from 26 to 287
present_time = fmins[m]
sim_start = fmins[m] - 600
sim_end = fmins[m] - 300
print(datetime.fromtimestamp(fmins[m]))
net = sumolib.net.readNet('../../Data/networks/SN_sample.net.xml')
inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)

2024-01-05 08:20:00


In [3]:
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
ch2pa = {'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'c30': 'i3'}
pa2ch = {'i0':['u00'], 'i1':[], 'i2':['u20'], 'i3':['c30', 'u30', 'u31', 'u32'], 'i6':[], 'i7':[], 'i8':[], 'i9':[]}
node_ids = sorted(inter_node.node_id.unique())
parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
child_ids = sorted(inter_node[inter_node.inter_type=='child'].node_id.unique())

print(inter2node)
print(node2inter)
print(ch2pa)
print(pa2ch)
print(node_ids)
print(parent_ids)
print(child_ids)

{175: 'u00', 176: 'i1', 177: 'u20', 178: 'c30', 201: 'i8', 202: 'i9', 206: 'i7', 210: 'i6'}
{'i0': 175, 'u00': 175, 'i1': 176, 'i2': 177, 'u20': 177, 'i3': 178, 'u30': 178, 'u31': 178, 'u32': 178, 'i8': 201, 'i9': 202, 'i7': 206, 'i6': 210, 'c30': 178}
{'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'c30': 'i3'}
{'i0': ['u00'], 'i1': [], 'i2': ['u20'], 'i3': ['c30', 'u30', 'u31', 'u32'], 'i6': [], 'i7': [], 'i8': [], 'i9': []}
['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32']
['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']
['c30', 'u00', 'u20', 'u30', 'u31', 'u32']


In [4]:
histid_dt = histid.copy()
histid_dt['start_dt'] = histid_dt['start_unix'].map(lambda x:datetime.fromtimestamp(x))
sdti3 = sorted(histid_dt[histid_dt.node_id=='i0'].start_dt.unique())
sdti3

NameError: name 'histid' is not defined

In [ ]:
print(fmins[m], datetime.fromtimestamp(fmins[m]))
histid = pd.read_csv(f'../../Data/tables/histids/histids_{fmins[m]}.csv', index_col=0)
match6 = pd.read_csv('../../Data/tables/matching/match6.csv', index_col=0)
histid = histid.reset_index(drop=True)
histid = histid.drop(columns=['inter_no'])
match6 = match6[['node_id', 'phase_no', 'ring_type', 'inc_edge', 'out_edge']].reset_index(drop=True)
display(histid)
display(match6)

1704410400 2024-01-05 08:20:00


node_id  start_unix  phas_A  phas_B  duration       inc_edge_A  \
0       i3  1704409510       1       1        38     571540304_02   
1       i3  1704409510       2       2        39     571556450_02   
2       i3  1704409510       3       3        42  571540303_02.21   
3       i3  1704409510       4       4        21    -571500475_01   
4       i9  1704409510       1       1        46     571510152_02   
..     ...         ...     ...     ...       ...              ...   
88      i8  1704410180       1       1        30    -571500569_01   
89      i8  1704410180       2       2        36     571500618_02   
90      i8  1704410180       3       3        18     571500617_02   
91      i8  1704410180       4       4        58     571500617_02   
92      i8  1704410180       5       5        18     571500583_01   

       out_edge_A       inc_edge_B       out_edge_B  
0    571556450_01     571556450_02     571540304_01  
1    571500475_01     571540304_02     571540303_01  
2    571556450_01  571540303_02.21     571500475_01  
3    571540303_01    -571500475_01     571540304_01  
4   -571510152_01     571510152_01  571510152_01.65  
..            ...              ...              ...  
88   571500583_02    -571500569_01     571500618_01  
89   571500583_02     571500618_02     571500617_01  
90   571500618_01     571500618_02     571500617_01  
91   571500618_01     571500617_02     571500569_01  
92   571500617_01     571500583_01     571500569_01  

[93 rows x 9 columns]

node_id  phase_no ring_type       inc_edge       out_edge
0        i0         1         A  -571542797_02   571500487_01
1        i0         1         B  -571500487_01   571542797_02
2        i0         2         A  -571500487_01   571545870_01
3        i0         2         B  -571542797_02   571510153_01
4        i0         3         A   571545870_02   571510153_01
..      ...       ...       ...            ...            ...
111     u60         2         B   571500535_02  -571500535_02
112     u60         3         A            NaN            NaN
113     u60         3         B            NaN            NaN
114     u60         4         A            NaN            NaN
115     u60         4         B            NaN            NaN

[116 rows x 5 columns]

In [ ]:
new_histids = []
for parent_id in parent_ids:
    for child_id in pa2ch[parent_id]:
        new_histid = histid.copy()[histid.node_id==parent_id]
        new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = match6[match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]
            if ~Arow[['inc_edge', 'out_edge']].isna().all().all():
                inc_edge = Arow.iloc[0].inc_edge
                out_edge = Arow.iloc[0].out_edge
                new_histid.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge, out_edge]
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            if ~Brow[['inc_edge', 'out_edge']].isna().all().all():
                inc_edge = Brow.iloc[0].inc_edge
                out_edge = Brow.iloc[0].out_edge
                new_histid.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge, out_edge]
            new_histid.loc[i, 'node_id'] = child_id
        new_histids.append(new_histid)

new_histids = pd.concat(new_histids)
sigtable = pd.concat([histid.copy(), new_histids])
sigtable = sigtable.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
display(sigtable)

node_id  start_unix  phas_A  phas_B  duration     inc_edge_A  \
0       c30  1704409510       1       1        38            NaN   
1       c30  1704409510       2       2        39   571542116_01   
2       c30  1704409510       3       3        42   571542116_01   
3       c30  1704409510       4       4        21   571542116_01   
4        i3  1704409510       1       1        38   571540304_02   
..      ...         ...     ...     ...       ...            ...   
195      i8  1704410180       1       1        30  -571500569_01   
196      i8  1704410180       2       2        36   571500618_02   
197      i8  1704410180       3       3        18   571500617_02   
198      i8  1704410180       4       4        58   571500617_02   
199      i8  1704410180       5       5        18   571500583_01   

           out_edge_A       inc_edge_B        out_edge_B  
0                 NaN              NaN               NaN  
1    -571542116_02.96  571542116_02.96  571542116_02.164  
2    -571542116_02.96  571542116_02.96  571542116_02.164  
3    -571542116_02.96  571542116_02.96  571542116_02.164  
4        571556450_01     571556450_02      571540304_01  
..                ...              ...               ...  
195      571500583_02    -571500569_01      571500618_01  
196      571500583_02     571500618_02      571500617_01  
197      571500618_01     571500618_02      571500617_01  
198      571500618_01     571500617_02      571500569_01  
199      571500617_01     571500583_01      571500569_01  

[200 rows x 9 columns]

In [ ]:
node_ids = sorted(sigtable.node_id.unique())
nodes = [net.getNode(node_id) for node_id in node_ids]
print(node_ids)
print(nodes)

['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32']
[<junction id="c30"/>, <junction id="i0"/>, <junction id="i1"/>, <junction id="i2"/>, <junction id="i3"/>, <junction id="i6"/>, <junction id="i8"/>, <junction id="i9"/>, <junction id="u00"/>, <junction id="u20"/>, <junction id="u30"/>, <junction id="u31"/>, <junction id="u32"/>]


In [ ]:
node2init = {}
for node in nodes:
    node_id = node.getID()
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        for j, cj in conns:
            if ci.getTo() == cj.getTo():
                continue
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in sigtable.iterrows():
    node_id = row['node_id']
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        pass
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        pass
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'
for node_id in node_ids:
    print(node_id, "".join(node2init[node_id]))

c30 rrrrrr
i0 grrrgrrrgrrrrrgrr
i1 grrrrrrgrr
i2 rrggrrr
i3 grrrrgrrrrgrrrrgrrrr
i6 grrrgrrrrgrrgrrr
i8 grrrrrrrgrrrgrrr
i9 rrrr
u00 ggggrgggg
u20 ggrggg
u30 ggggrggg
u31 ggggrggg
u32 gggggggr


In [ ]:
sigtable['init_state'] = sigtable['node_id'].map(node2init)
for i, row in sigtable.iterrows():
    node_id = row.node_id
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B
    state = copy.deepcopy(node2init)[node_id]

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        continue
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        continue
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)
sigtable = sigtable.dropna(subset='state')
sigtable = sigtable.reset_index(drop=True)
sigtable['phase_sumo'] = sigtable.groupby(['node_id', 'start_unix']).cumcount()
sigtable = sigtable[['node_id', 'start_unix', 'phase_sumo', 'duration', 'state']]
sigtable = sigtable.sort_values(by=['start_unix', 'node_id'])
sigtable_dt = sigtable.copy() #[sigtable.start_unix >= fmins[m]-420]
sigtable_dt['start_dt'] = sigtable_dt['start_unix'].apply(lambda x:datetime.fromtimestamp(x))
display(sigtable_dt)
# 시뮬레이션 시작시각 : 현재시각 - 600 = 08:10
# 시뮬레이션 종료시각 : 현재시각 - 300 = 08:15
# 현재시각        : present_time, PT = 08:20
# PT-900 ... PT-600 ... PT-300 ... PT

node_id  start_unix  phase_sumo  duration                 state  \
0       c30  1704409510           0        39                GGGGGG   
1       c30  1704409510           1        42                GGGGGG   
2       c30  1704409510           2        21                GGGGGG   
3        i3  1704409510           0        38  gGGGrgrrrrgGGGrgrrrr   
4        i3  1704409510           1        39  grrrGgrrrrgrrrGgrrrr   
..      ...         ...         ...       ...                   ...   
112      i8  1704410180           0        30      grrrrrrrgGGGgrrr   
113      i8  1704410180           1        36      grrrrrrrgrrrgGGG   
114      i8  1704410180           2        18      grrrGGGrgrrrgGGr   
115      i8  1704410180           3        58      grrrGGGGgrrrgrrr   
116      i8  1704410180           4        18      gGGGrrrrgrrrgrrr   

               start_dt  
0   2024-01-05 08:05:10  
1   2024-01-05 08:05:10  
2   2024-01-05 08:05:10  
3   2024-01-05 08:05:10  
4   2024-01-05 08:05:10  
..                  ...  
112 2024-01-05 08:16:20  
113 2024-01-05 08:16:20  
114 2024-01-05 08:16:20  
115 2024-01-05 08:16:20  
116 2024-01-05 08:16:20  

[117 rows x 6 columns]

In [ ]:
print(sim_start,   datetime.fromtimestamp(sim_start))
print(sim_end,     datetime.fromtimestamp(sim_end))
print(present_time,datetime.fromtimestamp(present_time))

1704409800 2024-01-05 08:10:00
1704410100 2024-01-05 08:15:00
1704410400 2024-01-05 08:20:00


In [ ]:
for node_id in sorted(sigtable_dt.node_id.unique()):
    sig1 = sigtable_dt[sigtable_dt.node_id==node_id]
    dt_min = sig1.start_dt.min()
    dt_max = sig1.start_dt.max()
    print(node_id, dt_min, dt_max)

c30 2024-01-05 08:05:10 2024-01-05 08:15:50
i0 2024-01-05 08:06:30 2024-01-05 08:12:10
i1 2024-01-05 08:07:10 2024-01-05 08:15:40
i2 2024-01-05 08:08:40 2024-01-05 08:14:20
i3 2024-01-05 08:05:10 2024-01-05 08:15:50
i6 2024-01-05 08:11:50 2024-01-05 08:14:40
i8 2024-01-05 08:11:00 2024-01-05 08:16:20
i9 2024-01-05 08:05:10 2024-01-05 08:16:00
u00 2024-01-05 08:06:30 2024-01-05 08:12:10
u20 2024-01-05 08:08:40 2024-01-05 08:14:20
u30 2024-01-05 08:05:10 2024-01-05 08:15:50
u31 2024-01-05 08:05:10 2024-01-05 08:15:50


In [ ]:
sig1 = sigtable_dt[sigtable_dt.node_id=='i2']
dts = sorted(sig1.start_dt.unique())
print(dt_min)
print(dt_min.strftime('%H:%M:%S'))

In [ ]:
sig1 = sigtable_dt[sigtable_dt.node_id=='i2']
dt_min = sig1.start_dt.min()
print(dt_min)
print(dt_min.strftime('%H:%M:%S'))

2024-01-05 08:08:40
08:08:40


In [ ]:
for node_id in parent_ids:
    sig1 = sigtable_dt[sigtable_dt.node_id==node_id]
    dt_min = sig1.start_dt.min()
    dt_max = sig1.start_dt.max()
    print(node_id, dt_min, dt_max)

i0 2024-01-05 08:06:30 2024-01-05 08:12:10
i1 2024-01-05 08:07:10 2024-01-05 08:15:40
i2 2024-01-05 08:08:40 2024-01-05 08:14:20
i3 2024-01-05 08:05:10 2024-01-05 08:15:50
i6 2024-01-05 08:11:50 2024-01-05 08:14:40
i7 NaT NaT
i8 2024-01-05 08:11:00 2024-01-05 08:16:20
i9 2024-01-05 08:05:10 2024-01-05 08:16:00


In [ ]:
print(sigtable.start_unix.max() - sigtable.start_unix.min())
print(datetime.fromtimestamp(fmins[m - 1]))
print(datetime.fromtimestamp(fmins[m]))
print(datetime.fromtimestamp(sigtable.start_unix.max()))
print(datetime.fromtimestamp(sigtable.start_unix.min()))

670
2024-01-05 08:15:00
2024-01-05 08:20:00
2024-01-05 08:16:20
2024-01-05 08:05:10


In [ ]:
sigtable1 = sigtable.copy()


In [ ]:
sorted(sigtable.node_id.unique())

['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31']

In [ ]:
strings = ['<tlLogics>\n']
for key, group in sigtable.groupby(['start_unix', 'node_id']):
    start_unix = key[0]
    node_id = key[1]
    strings.append(f'    <tlLogic id="{node_id}" type="traffic_light" programID="{key}" offset="{start_unix}">\n')
    for i, row in group.iterrows():
        duration = row.duration
        state = row.state
        strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
    strings.append('    </tlLogic>\n')


In [ ]:
strings = ['<tlLogics>\n']
for key, group in sigtable.groupby(['start_unix', 'node_id']):
    start_unix = key[0]
    node_id = key[1]
    strings.append(f'    <tlLogic id="{node_id}" type="traffic_light" programID="{key}" offset="{start_unix}">\n')
    for i, row in group.iterrows():
        duration = row.duration
        state = row.state
        strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
    strings.append('    </tlLogic>\n')
strings.append('</tlLogics>')
strings = ''.join(strings)
# 저장
path_output = '../../Data/networks/SN_sample.tll.xml'
with open(path_output, 'w') as f:
    f.write(strings)
print(strings)

<tlLogics>
    <tlLogic id="c30" type="traffic_light" programID="(1704409510, 'c30')" offset="1704409510">
      <phase duration="39" state="GGGGGG"/>
      <phase duration="42" state="GGGGGG"/>
      <phase duration="21" state="GGGGGG"/>
    </tlLogic>
    <tlLogic id="i3" type="traffic_light" programID="(1704409510, 'i3')" offset="1704409510">
      <phase duration="38" state="gGGGrgrrrrgGGGrgrrrr"/>
      <phase duration="39" state="grrrGgrrrrgrrrGgrrrr"/>
      <phase duration="42" state="grrrrgrrrrgrrrrgGGGG"/>
      <phase duration="21" state="grrrrgGGGGgrrrrgrrrr"/>
    </tlLogic>
    <tlLogic id="i9" type="traffic_light" programID="(1704409510, 'i9')" offset="1704409510">
      <phase duration="46" state="GGGG"/>
    </tlLogic>
    <tlLogic id="u30" type="traffic_light" programID="(1704409510, 'u30')" offset="1704409510">
      <phase duration="21" state="ggggGggg"/>
    </tlLogic>
    <tlLogic id="u31" type="traffic_light" programID="(1704409510, 'u31')" offset="1704409510">
 

In [ ]:
strings = ['<tlLogics>\n']
for key, group in sigtable.groupby(['start_unix', 'node_id']):
    start_unix = key[0]
    node_id = key[1]
    strings.append(f'    <tlLogic id="{node_id}" type="traffic_light" programID="{key}" offset="{start_unix}">\n')
    for i, row in group.iterrows():
        duration = row.duration
        state = row.state
        strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
    strings.append('    </tlLogic>\n')
strings.append('</tlLogics>')
strings = ''.join(strings)
# 저장
path_output = '../../Data/networks/SN_sample.tll.xml'
with open(path_output, 'w') as f:
    f.write(strings)
print(strings)

<tlLogics>
    <tlLogic id="c30" type="traffic_light" programID="(1704409510, 'c30')" offset="1704409510">
      <phase duration="39" state="GGGGGG"/>
      <phase duration="42" state="GGGGGG"/>
      <phase duration="21" state="GGGGGG"/>
    </tlLogic>
    <tlLogic id="i3" type="traffic_light" programID="(1704409510, 'i3')" offset="1704409510">
      <phase duration="38" state="gGGGrgrrrrgGGGrgrrrr"/>
      <phase duration="39" state="grrrGgrrrrgrrrGgrrrr"/>
      <phase duration="42" state="grrrrgrrrrgrrrrgGGGG"/>
      <phase duration="21" state="grrrrgGGGGgrrrrgrrrr"/>
    </tlLogic>
    <tlLogic id="i9" type="traffic_light" programID="(1704409510, 'i9')" offset="1704409510">
      <phase duration="46" state="GGGG"/>
    </tlLogic>
    <tlLogic id="u30" type="traffic_light" programID="(1704409510, 'u30')" offset="1704409510">
      <phase duration="21" state="ggggGggg"/>
    </tlLogic>
    <tlLogic id="u31" type="traffic_light" programID="(1704409510, 'u31')" offset="1704409510">
 